In [1]:
from pymongo import MongoClient
from pprint import pprint
import igraph
import numpy as np
import scipy
import scipy.sparse as sp
from scipy.sparse.linalg import eigsh, eigs
from scipy.sparse import csgraph

import pandas as pd
import sys
import pymongo

try:
    client = MongoClient('localhost', 27017) # host, port
except ConnectionFailure as e:
    sys.stderr.write("Could not connect to MongoDB: %s" % e)
    sys.exit(1)

In [2]:
# get database with all tweets
#db = client.tweets_database


#db.filtered_tweets.drop()

# new database with cleaned tweets (without Retweets, in english)
filtered_treated_tweets = client.tweets_database.filtered_treated_tweets

client.tweets_database.collection_names()

['cleaned_tweets',
 'filtered_tweets_noRetweets_english',
 'users',
 'filtered_treated_tweets',
 'tweets']

In [4]:
#client.tweet_database.stats()

In [3]:

#pymongo.version
#client.tweets_database.filtered_treated_tweets.create_index( [{ 'user.screen_name': 1 , 
#                                                               'retweeted_status.user.screen_name': 1,
#                                                               'number_of_weeks': 1}] )
client.tweets_database.filtered_treated_tweets.create_index([('user.screen_name', 1), 
                                                             ('retweeted_status.user.screen_name', 1),
                                                             ('number_of_weeks', 1)], 
                                                              name='userName_retweetName_nWeek')
#create_index([(name_index, order)])

'userName_retweetName_nWeek'

In [72]:
# get unique users and users of the retweets twittering in week 1
#users_tweet = filtered_treated_tweets.distinct('user.screen_name', {'number_of_weeks' : 1}) #user.id
#users_retweet = filtered_treated_tweets.distinct('retweeted_status.user.screen_name', {'number_of_weeks' : 1})
#print(users_tweet)
#print(len(users_tweet))
#print(len(users_retweet))

#users = set().union(users_tweet, users_retweet)
#n_users = len(users)

#print(n_users)

users = set().union( [v['_id'] for v in filtered_treated_tweets.aggregate( [ 
                                            {'$match': {'number_of_weeks' : 1}},
                                            {"$group" : { "_id" : "$user.screen_name" } }
                                           
                                         ] )
                      ],
                     [v['_id'] for v in filtered_treated_tweets.aggregate( [ 
                                            {'$match': {'number_of_weeks' : 1}},
                                            {"$group" : { "_id" : "$retweeted_status.user.screen_name" } }
                                           
                                         ] )
                      ]
                   )
print(len(users))

2441
521
2922
2922


In [4]:
#pd.__version__

# create dictionary: each user name corresponds to one unique number between 0 and n_users

count = 0
userToInt_dict = {}
for user in users:
    userToInt_dict[user] = count
    count += 1
#pprint(userToInt_dict)

intToUser_dict = {v: k for k,v in userToInt_dict.items()}
#intToUser_dict


NameError: name 'users' is not defined

In [8]:
import scipy.sparse as sp
from scipy.sparse.linalg import eigsh, eigs
# create matrix users x users 

rows = [1,1,1,3,3,5]
columns = [1,2,3,1,2,6]
data = [1,2,1,1,3,1]
A_sp = sp.lil_matrix((7,7))

A_sp[1,1] = 1
A_sp[1,2] = 2
A_sp[1,3] = 1
A_sp[3,1] = 1
A_sp[3,2] = 3
A_sp[5,6] = 1

#blabla = A_sp.toarray()
#print(blabla)

a = np.array([0,1,1,1,0,0,0])
ind = [False, True, True, True, False, False, False]
print(A_sp.toarray())
print("")
print(A_sp.tocsr()[a==1, :][:, a==1])


eigenvalues, eigenvectors = np.linalg.eig(A_sp.toarray())
print("eigval:", eigenvalues)
print("eigvec:", eigenvectors)
eigenvalues, eigenvectors = eigs(A_sp, k=2, which='LM')
print("")
print("eigval sparse:", eigenvalues)
print("eigvec:", eigenvectors)
eigenvalues, eigenvectors = eigsh(A_sp, k=2, which='LM')
print("")
print("eigval symm:", eigenvalues)
print("eigvec:", eigenvectors)
# create matrix users x users 
#A_df = pd.DataFrame(np.zeros((n_users, n_users)), columns = users, index = users)
#A_sp = sp.csr_matrix(np.zeros((n_users, n_users)))#.toarray()
#A_sp = sp.lil_matrix(np.zeros((n_users, n_users)))#.toarray()

print("INFO: adjacency matrix created. ")
#print("\t Info df:", A_df.info())

print(A_sp.get_shape())

[[0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 2. 1. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 3. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 0.]
 [0. 0. 0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 0. 0. 0.]]

  (0, 0)	1.0
  (0, 1)	2.0
  (0, 2)	1.0
  (2, 0)	1.0
  (2, 1)	3.0
eigval: [-0.61803399  1.61803399  0.          0.          0.          0.
  0.        ]
eigvec: [[ 0.00000000e+000  0.00000000e+000  1.00000000e+000  0.00000000e+000
   0.00000000e+000  0.00000000e+000  0.00000000e+000]
 [ 5.25731112e-001 -8.50650808e-001  0.00000000e+000 -9.04534034e-001
   0.00000000e+000  0.00000000e+000  0.00000000e+000]
 [ 0.00000000e+000  0.00000000e+000  0.00000000e+000  3.01511345e-001
   0.00000000e+000  0.00000000e+000  0.00000000e+000]
 [-8.50650808e-001 -5.25731112e-001  0.00000000e+000  3.01511345e-001
   0.00000000e+000  0.00000000e+000  0.00000000e+000]
 [ 0.00000000e+000  0.00000000e+000  0.00000000e+000  0.00000000e+000
   1.00000000e+000  0.00000000e+000  0.00000000e+000]
 [ 0.00000000e+000  0.00000000e+000  0.00000000e+0

In [80]:
# calculate co-citation network
C = A_sp.transpose() * A_sp
#print(C.toarray())
C.toarray()

array([[ 0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  2.,  5.,  1.,  0.,  0.,  0.],
       [ 0.,  5., 13.,  2.,  0.,  0.,  0.],
       [ 0.,  1.,  2.,  1.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  0.],
       [ 0.,  0.,  0.,  0.,  0.,  0.,  1.]])

In [87]:
C.get_shape()

(7, 7)

In [82]:
# calculate connected components:
from scipy.sparse import csgraph
connected_components = csgraph.connected_components(A_sp, directed=True)
connected_components

(5, array([0, 1, 1, 1, 2, 3, 4]))

In [83]:
indices = [i for i, comp in enumerate(connected_components[1]) if comp == 4]
print(indices)
#connected_components[1][1010]


[intToUser_dict[user] for user in indices]

[6]


['DILBAGS35721592']

In [29]:
# get submatrix
# TODO: maybe directly transform to sparse again
submatrix = A_sp.toarray()[connected_components[1] == 1, :][:, connected_components[1] == 1]
submatrix.shape

(219, 219)

In [84]:
# sort connected_components
countFrequenciesComponents = np.bincount(connected_components[1])
countFrequenciesComponents


array([1, 3, 1, 1, 1], dtype=int64)

In [85]:
sorted_labels = np.argsort(countFrequenciesComponents)[::-1]
sorted_labels

array([1, 4, 3, 2, 0], dtype=int64)

In [6]:
def calculate_score(M_sp, intToUser_dict):
    
    # get total number of nodes/users
    N = M_sp.get_shape()[0]
    
    # calculate connected components of sparse matrix
    connected_components = csgraph.connected_components(M_sp, directed=True)
    print("connected_components:", connected_components[0])
    
    # count number of nodes/users in each component
    countFrequenciesComponents = np.bincount(connected_components[1])
    #print("countFrequenciesComponents:", countFrequenciesComponents)

    unique, counts = np.unique(countFrequenciesComponents, return_counts=True)
    #print("Count occurences of groups", dict(zip(unique, counts)))
    
    # sort connected components from most connected to not connected at all
    sorted_labels = np.argsort(countFrequenciesComponents)[::-1]
    #print("sorted labels:", sorted_labels)
    
    # define vector containing all scores for each node
    v = pd.DataFrame(columns=["score"])

    for ind in sorted_labels:
        # when we see a single component of  size one we can break, 
        #since all other components after will be one too (array is sorted!)
        if countFrequenciesComponents[ind] != 1:
            #print("ind:", ind)
            #print("countfreq:", countFrequenciesComponents[ind])
            N_comp = countFrequenciesComponents[ind]

            # get list of indices of the current connected composent representing the users
            indices_user_comp = [i for i, comp in enumerate(connected_components[1]) if comp == ind]
            #print("length of indices_ user:", len(indices_user_comp))


            # get submatrix of current component
            #submatrix = M_sp.toarray()[connected_components[1] == ind, :][:, connected_components[1] == ind]
            submatrix = M_sp.tocsr()[connected_components[1] == ind, :][:, connected_components[1] == ind]
        
            #print("shape submatrix:", submatrix.shape)
            #print(submatrix)

            # k must be less than ndim(A)-1
            #eigenvalues, eigenvectors = np.linalg.eig(submatrix)
            if submatrix.get_shape()[0] > 10:
                eigenvalues, eigenvectors = eigs(submatrix, k=2, which='LM')
            else:
                eigenvalues, eigenvectors = np.linalg.eig(submatrix.toarray())


            # get index of maximum eigen value
            max_eigval_ind = np.argmax(eigenvalues)
            #print("max eigen value:", eigenvalues[max_eigval_ind], ", index:", max_eigval_ind)
            #print("max eigen vector:")
            #print(eigenvectors[:,max_eigval_ind])

            # normalise eigen vector for maximum eigen value s.t. sum of vector = 1
            max_eigvec_norm = eigenvectors[:,max_eigval_ind]/sum(eigenvectors[:,max_eigval_ind])
            #print("normalised max eigen vector:")
            #print(max_eigvec_norm)

            # weight-average vectors s.t. score of each node is weighted according to the size of the component
            # which it is found, thus ensuring that the scores are comparable and that we do not discard
            # information from the smaller components
            users_of_component = [intToUser_dict[user] for user in indices_user_comp]

            max_eigvec_norm_weighted = pd.DataFrame((N_comp/N)*max_eigvec_norm, index=users_of_component,
                                                    columns=["score"])
            #print("Weighted eig vec:")
            #print(max_eigvec_norm_weighted)
            #print("")

            # append scores from current connected composant to global vector v containing all scores
            v = pd.concat([v,max_eigvec_norm_weighted], axis=0)

        else:
            break
    
    return v

In [7]:
import scipy.sparse as sp
# create matrix users x users 



# create matrix users x users 
#A_sp = sp.lil_matrix(np.zeros((n_users, n_users)))#.toarray()

#print("INFO: adjacency matrix created. ")
#print("\t Info df:", A_df.info())

nWeek = 1
# fill retweet adjacency matrix with number of retweets
tweets_per_week = filtered_treated_tweets.find({'number_of_weeks' : nWeek}, {"user.screen_name":1, "retweeted_status.user.screen_name":1})
#for tweet in tweets_per_week:
#    print(tweet)
#    print("")
#print("INFO: got tweets per week, size:", sys.getsizeof(tweets_per_week))

#i = 1
#for tweet in tweets_per_week:
#    # only for retweets: add +1 when user of tweet retweeted other user
#    if "retweeted_status" in tweet.keys():
        #print("who: ", tweet["user"]["screen_name"], userToInt_dict[tweet["user"]["screen_name"]] )
        #print("from: ", tweet["retweeted_status"]["user"]["screen_name"],userToInt_dict[tweet["retweeted_status"]["user"]["screen_name"]] )
        #print("")
#        who_retweeted = userToInt_dict[tweet["user"]["screen_name"]]
#        retweeted_from = userToInt_dict[tweet["retweeted_status"]["user"]["screen_name"]]
#        A_sp[who_retweeted, retweeted_from] += 1
        #A_df.at[tweet["user"]["screen_name"], tweet["retweeted_status"]["user"]["screen_name"]] += 1
        #A_df_sp.at[tweet["user"]["screen_name"], tweet["retweeted_status"]["user"]["screen_name"]] += 1

        
#    if i % 1000 == 0:
#        print(i)
    
#    i +=1
    #if i == 10:
    #    break
    
       
#print("INFO: number of non zero entries:", A_sp.count_nonzero())
#        
#print("INFO: adjacency matrix filled. ")
#print("INFO: Memory usage of A (in MB):", A_sp.data.nbytes/1024)


In [12]:
# dictionary in which we save the scores over the weeks
authority_dict = {}
hub_dict = {}


nWeek = 1
while(True):
    print("----------------WEEK {} -----------------:".format(nWeek))
    # get unique users and users of the retweets twittering in week 1
    #users_tweet = filtered_treated_tweets.distinct('user.screen_name', {'number_of_weeks' : nWeek}) #user.id
    #users_retweet = filtered_treated_tweets.distinct('retweeted_status.user.screen_name', 
    #                                                 {'number_of_weeks' : nWeek})

    #users = set().union(users_tweet, users_retweet)
    
    users = set().union( [v['_id'] for v in filtered_treated_tweets.aggregate( [ 
                                                {'$match': {'number_of_weeks' : nWeek}},
                                                {"$group" : { "_id" : "$user.screen_name" } }

                                             ] )
                          ],
                         [v['_id'] for v in filtered_treated_tweets.aggregate( [ 
                                                {'$match': {'number_of_weeks' : nWeek}},
                                                {"$group" : { "_id" : "$retweeted_status.user.screen_name" } }

                                             ] )
                          ]
                       )

    n_users = len(users)
    #print("number of users:", n_users)

    print("INFO: Number of nodes total:", n_users)

    
    # create dictionary: each user name corresponds to one unique number between 0 and n_users

    count = 0
    userToInt_dict = {}
    for user in users:
        userToInt_dict[user] = count
        count += 1

    intToUser_dict = {v: k for k,v in userToInt_dict.items()}
    #intToUser_dict
    print("INFO: Created dictionaries for conversion integer <-> user")
    print("\t Length of dict:", len(intToUser_dict))
    
    # break at last week when there is no tweet anymore
    if n_users < 20:
        break
      
    
    # create matrix users x users 
    #A_sp = sp.lil_matrix(np.zeros((n_users, n_users)))#.toarray()
    A_sp = sp.lil_matrix(sp.coo_matrix((n_users, n_users)))#.toarray()

    # fill retweet adjacency matrix with number of retweets
    tweets_per_week = filtered_treated_tweets.find({'number_of_weeks' : nWeek}, {"user.screen_name":1, "retweeted_status.user.screen_name":1})
    #print("INFO: got tweets per week, size:", sys.getsizeof(tweets_per_week))

    i = 1
    for tweet in tweets_per_week:
        # only for retweets: add +1 when user of tweet retweeted other user
        if "retweeted_status" in tweet.keys():
            who_retweeted = userToInt_dict[tweet["user"]["screen_name"]]
            retweeted_from = userToInt_dict[tweet["retweeted_status"]["user"]["screen_name"]]
            A_sp[who_retweeted, retweeted_from] += 1

       
    print("INFO: number of non zero entries in adjacency matr:", A_sp.count_nonzero())        
    print("INFO: Memory usage of A (in KB):", A_sp.data.nbytes/1024)

    
    N = n_users
    

    # Co-citation network
    # ----------------------------------------------------------------
    C = A_sp.transpose() * A_sp

    score_authority = calculate_score(C, intToUser_dict)
    #print("INFO: Score calculated:")
    #print(score_authority)
    print("Authority score length: ", len(score_authority))
    
    
    for user, row in score_authority.iterrows():
        if user not in authority_dict.keys():
            authority_dict[user] = [(nWeek, row.score)]
        else:
            authority_dict[user].append((nWeek, row.score))
    
    
    # Bibliographic network
    # ------------------------------------------------------------------
#    B = A_sp * A_sp.transpose()
    
#    score_hub = calculate_score(B, intToUser_dict)
#    print("INFO: Score calculated")
    #print(score_authority)
#    print("\tlength: ", len(score_hub))

#    for user, row in score_hub.iterrows():
#        if user not in hub_dict.keys():
#            hub_dict[user] = [(nWeek, row.score)]
#        else:
#            hub_dict[user].append((nWeek, row.score))
    
    nWeek += 1
    print("")
    
    


----------------WEEK 1 -----------------:
INFO: Number of nodes total: 2922
INFO: Created dictionaries for conversion integer <-> user
	 Length of dict: 2922
INFO: number of non zero entries in adjacency matr: 2502
INFO: Memory usage of A (in KB): 22.828125
connected_components: 2873
Authority score length:  74

----------------WEEK 2 -----------------:
INFO: Number of nodes total: 29417
INFO: Created dictionaries for conversion integer <-> user
	 Length of dict: 29417
INFO: number of non zero entries in adjacency matr: 20819
INFO: Memory usage of A (in KB): 229.8203125
connected_components: 28533
Authority score length:  948

----------------WEEK 3 -----------------:
INFO: Number of nodes total: 45644
INFO: Created dictionaries for conversion integer <-> user
	 Length of dict: 45644
INFO: number of non zero entries in adjacency matr: 29170
INFO: Memory usage of A (in KB): 356.59375
connected_components: 44142
Authority score length:  1612

----------------WEEK 4 -----------------:
INF

connected_components: 41623
Authority score length:  1597

----------------WEEK 27 -----------------:
INFO: Number of nodes total: 55264
INFO: Created dictionaries for conversion integer <-> user
	 Length of dict: 55264
INFO: number of non zero entries in adjacency matr: 37278
INFO: Memory usage of A (in KB): 431.75
connected_components: 53641
Authority score length:  1726

----------------WEEK 28 -----------------:
INFO: Number of nodes total: 52673
INFO: Created dictionaries for conversion integer <-> user
	 Length of dict: 52673
INFO: number of non zero entries in adjacency matr: 36473
INFO: Memory usage of A (in KB): 411.5078125
connected_components: 50960
Authority score length:  1838

----------------WEEK 29 -----------------:
INFO: Number of nodes total: 87942
INFO: Created dictionaries for conversion integer <-> user
	 Length of dict: 87942
INFO: number of non zero entries in adjacency matr: 70449
INFO: Memory usage of A (in KB): 687.046875
connected_components: 84066
Authority

In [8]:
#authority_dict



#print(datetime.datetime.now().strftime(format))
for k, v in authority_dict.items():
    s = k+";"
    for score in v:
        s += str(score[0])+";"+str(score[1])+";"

    s += "\n"
    print(s)


In [21]:
import datetime
format = "%Y-%m-%d_%H-%M-%S"

pathname = "authority_scores_week13_33__{}.csv".format(datetime.datetime.now().strftime(format))
with open(pathname,'w') as file:
    for k, v in authority_dict.items():
        s = k+";"
        for score in v:
            s += str(score[0])+";"+str(score[1])+";"

        s += "\n"
        file.write(s)

In [9]:
#authority_dict

In [29]:

authority_dict_true = authority_dict.copy()
with open("authority_scores_week1_12__2018-05-23_15-52-01.csv", 'r') as file:
    for line in file:
        line = line.split(";")
        key = line[0]
        value = line[1:-1]
        
        i = 0
        temp = []
        while i < len(value):
            temp.append((value[i], value[i+1]))
            i += 2 
        value = temp
        
        if key in authority_dict.keys():
            for tup in authority_dict[key]:
                value.append(tup)
            authority_dict[key] = value
        else:
            authority_dict[key] = value
            
        #print(key)
        #print(value)
        

  
        
        

In [10]:
#authority_dict


In [31]:
format = "%Y-%m-%d_%H-%M-%S"

pathname = "authority_scores__{}.csv".format(datetime.datetime.now().strftime(format))
with open(pathname,'w') as file:
    for k, v in authority_dict.items():
        s = k+";"
        for score in v:
            s += str(score[0])+";"+str(score[1])+";"

        s += "\n"
        file.write(s)

In [13]:
#calculate aggregated score
aggregated_scores = []
for key, values in authority_dict.items():
    print(key)
    print(values)
    sum_scores = 0
    for tup in values:
        if isinstance(tup[1], str) :
            sum_scores += np.complex(tup[1]).real
        else:
            sum_scores += np.array(tup[1]).real
        
    print(sum_scores)
    print(len(values))
    print("")

    aggregated_scores.append((key, sum_scores, len(values)))
    #break
aggregated_scores = sorted(aggregated_scores, key=lambda x: x[1], reverse=True)
aggregated_scores

Bharathgyan
[(29, (3.2662458637960525e-08+0j))]
3.2662458637960525e-08
1

kathleennotkat
[(31, (1.7951454958900405e-08+0j))]
1.7951454958900405e-08
1

RepKevinCramer
[(13, (3.921271073903458e-08+0j))]
3.921271073903458e-08
1

AHealthBlog
[(2, (1.3076769748648978e-11+0j)), (3, (3.2156855373271617e-10+0j)), (4, (1.4160425633685047e-09+0j)), (5, (1.2388061166736205e-07+0j)), (6, (4.996677275489558e-15+0j)), (7, (4.335932747430116e-08+0j)), (8, (5.535519283789517e-09+0j)), (9, (2.744655310322279e-08+0j)), (10, (1.5936831460490421e-07+0j)), (11, (2.813171580222229e-17+0j)), (12, (2.2510700285193392e-08+0j)), (13, (1.1209763325416418e-08+0j)), (14, (1.5242600515232196e-08+0j)), (15, (4.8927525011929854e-08+0j)), (16, (2.4387571867595177e-06+0j)), (17, (6.277378203468513e-12+0j)), (18, (1.3502084738674626e-13+0j)), (19, (1.1134161726271268e-09+0j)), (20, (8.133911656696196e-13+0j)), (21, (1.9137866771453393e-15+0j)), (22, (4.0891085589127714e-07+0j)), (23, (2.6232200392395297e-10+0j)), (24, (

1

sophiexmasonx
[(6, (7.887690347178108e-07+0j))]
7.887690347178108e-07
1

ChupKerEshoo
[(4, (1.6133920791473667e-05+0j))]
1.6133920791473667e-05
1

JosephCafazzo
[(29, (6.10841426129981e-06+0j))]
6.10841426129981e-06
1

Senology
[(26, (1.471214951000373e-17+0j))]
1.471214951000373e-17
1

Lana_Bandoim
[(13, (1.2065539362020225e-05+0j))]
1.2065539362020225e-05
1

chaithradelant2
[(6, (5.267359931807524e-05+0j))]
5.267359931807524e-05
1

QCWirelessReach
[(27, (6.940050354788665e-15+0j))]
6.940050354788665e-15
1

itsmariahduhhhh
[(32, (2.266653795202086e-08+0j))]
2.266653795202086e-08
1

CatsShelter
[(10, (1.5504463121763424e-17+0j))]
1.5504463121763424e-17
1

PsoriasisIFPA
[(4, (1.424030406332453e-19+0j)), (6, (5.595738720954785e-19+0j))]
7.019769127287238e-19
2

cutestsquid
[(5, 2.142778094587596e-05)]
2.142778094587596e-05
1

WestsideAnt317
[(23, 2.233738384560401e-05)]
2.233738384560401e-05
1

biggA_04
[(13, 1.0061760040140847e-05)]
1.0061760040140847e-05
1

JDRFwny
[(27, (1.99938434

1.2350730212420245e-06
1

absuRd_Nurse
[(10, (3.766357642898424e-11+0j)), (19, (2.804740229675115e-06+0j))]
2.804777893251544e-06
2

Steve_Engage
[(24, (2.3920296604826096e-18+0j))]
2.3920296604826096e-18
1

GFFemale
[(20, (2.4793792014150647e-12+0j))]
2.4793792014150647e-12
1

3112Mel
[(7, (1.7289575004064986e-13+0j))]
1.7289575004064986e-13
1

alexandramusic
[(7, (1.0474354451100828e-09+0j))]
1.0474354451100828e-09
1

DrJiayingZhu
[(18, (1.952204178854652e-17+0j))]
1.952204178854652e-17
1

michieworth
[(25, (1.3242020231516255e-10+0j))]
1.3242020231516255e-10
1

RachelOLindley
[(18, (6.61945580664461e-15+0j))]
6.61945580664461e-15
1

RichardBejah
[(8, (2.2690921838077365e-18+0j))]
2.2690921838077365e-18
1

laniecarter_
[(31, (8.532504235888156e-08+0j))]
8.532504235888156e-08
1

MTEschoolnurse
[(29, 1.1371130972686543e-05)]
1.1371130972686543e-05
1

Adeel_A_Sham
[(6, (6.883096979123064e-11+0j))]
6.883096979123064e-11
1

CanadaProtPlan
[(27, (9.887356430925722e-16+0j))]
9.8873564309257

2.1710340635244567e-05
1

pridgetteseiuli
[(12, (7.2069998420868195e-16+0j))]
7.2069998420868195e-16
1

acbrom
[(9, (9.057224595370911e-12+0j))]
9.057224595370911e-12
1

smallcellhub
[(9, 2.0958654106310594e-05)]
2.0958654106310594e-05
1

CarlaYoung
[(20, 8.851349006499989e-07), (21, (0.0004225736315368048+0j))]
0.0004234587664374548
2

MobilityCareAid
[(10, 2.1684133479994613e-05), (11, (1.755796241411885e-19+0j)), (12, (2.9733085712921627e-17+0j)), (13, (9.191646911819227e-12+0j)), (15, (3.4931765041655633e-11+0j)), (20, 3.718941031541268e-05), (21, (7.694456515978967e-13+0j)), (22, (3.2928560742596935e-11+0j)), (24, (2.729353366839945e-13+0j)), (29, (6.279914291014103e-10+0j)), (30, (-1.3172485943203913e-20-0j)), (31, (5.4350267429198956e-21+0j)), (32, (4.60614668735266e-13+0j))]
5.887425034183465e-05
13

SEHTA_UK
[(2, 2.596906627121087e-05)]
2.596906627121087e-05
1

Longreads
[(22, (4.123046151462058e-07+0j)), (24, (7.60855941583294e-15+0j)), (27, (-7.841324037575977e-21+0j)), (28,

[(8, (4.290300715522202e-18+0j))]
4.290300715522202e-18
1

KillerOrangeCat
[(5, (3.106408265378409e-08+0j))]
3.106408265378409e-08
1

__LightsPlease
[(12, (3.471533637677888e-16+0j))]
3.471533637677888e-16
1

ryancey2000
[(3, (2.5387303941277825e-11+0j))]
2.5387303941277825e-11
1

pannybear73
[(30, (2.6171674500512802e-06+0j))]
2.6171674500512802e-06
1

Mediosa_ng
[(16, (6.294047971389814e-11+0j)), (29, (2.932454269283411e-08+0j))]
2.938748317254801e-08
2

drstclaire
[(7, 1.51857039418799e-05), (17, (3.091082025836464e-12+0j)), (29, (9.972718514782299e-08+0j))]
1.5285434218109748e-05
3

OITable
[(26, (1.8796864806877206e-12+0j))]
1.8796864806877206e-12
1

AdelesBabyDaddy
[(24, (3.379367138100019e-15+0j))]
3.379367138100019e-15
1

BodmanSian
[(29, (1.1401612280568145e-07+0j))]
1.1401612280568145e-07
1

thorrungovind
[(7, (1.632038692923492e-14+0j))]
1.632038692923492e-14
1

KateIsabelle24
[(26, (1.4620035652935297e-17+0j))]
1.4620035652935297e-17
1

EeHRN
[(2, (-6.269244853276367e-20+0j

...

1.5726408201346523e-08
3

DaanDeWit
[(21, (5.80484712286887e-10+0j))]
5.80484712286887e-10
1

hadassz
[(13, (-9.077268484922641e-20-0j))]
-9.077268484922641e-20
1

racheldmatos
[(23, 2.5066717918625847e-05)]
2.5066717918625847e-05
1

health_tips_365
[(3, 3.948320932358857e-05), (6, (6.87258268102464e-11+0j)), (7, (4.496920887016473e-19+0j)), (10, (1.3035584782855344e-09+0j))]
3.9484581607894106e-05
4

GregTay2233
[(22, (4.08699780404323e-07+0j))]
4.08699780404323e-07
1

wlfsct
[(29, (2.424617455163074e-07+0j))]
2.424617455163074e-07
1

globalnews
[(12, (3.3329310158577904e-07+0j)), (14, (6.784241210652592e-06+0j)), (25, (1.1419118909742e-13+0j)), (26, (8.323497040243557e-20+0j)), (29, (3.3849606787413775e-06+0j))]
1.050249510517102e-05
5

TandemJobs
[(27, (3.9569520596572164e-15+0j)), (29, (1.8068086060829732e-08+0j))]
1.806809001778179e-08
2

NoshGKitchen
[(27, 1.8094962362478285e-05)]
1.8094962362478285e-05
1

Thepapaziglar
[(25, (-1.0382642792575948e-20+0j))]
-1.0382642792575948e-20

[(18, 1.7247029199220433e-05)]
1.7247029199220433e-05
1

tailopez
[(8, (6.529646658841294e-08+0j))]
6.529646658841294e-08
1

ClearlightAus
[(5, 2.811990326753276e-05)]
2.811990326753276e-05
1

comforcarehome
[(26, (2.9437080631023534e-16+0j))]
2.9437080631023534e-16
1

aracel1aguilar
[(31, (2.559852869828675e-07+0j))]
2.559852869828675e-07
1

NNInstitute
[(21, (6.14357388223253e-10+0j))]
6.14357388223253e-10
1

CenterforPrev
[(14, 2.3389624362632738e-05)]
2.3389624362632738e-05
1

kat__evans
[(18, 1.3827261477325858e-05)]
1.3827261477325858e-05
1

danimath616
[(11, 2.742449888032917e-05)]
2.742449888032917e-05
1

GiftedBacon
[(21, (6.072095177065392e-05+0j))]
6.072095177065392e-05
1

WestHantsCCG
[(29, (1.8700753420801862e-07+0j))]
1.8700753420801862e-07
1

DrTedros
[(20, (1.6353070445376922e-12+0j))]
1.6353070445376922e-12
1

Zen0469
[(22, (4.1216719897747244e-07+0j))]
4.1216719897747244e-07
1

MattsMentions
[(31, (8.532673564291447e-08+0j))]
8.532673564291447e-08
1

DanielJDrucker
[(

[(32, (1.5829926675715054e-07+0j))]
1.5829926675715054e-07
1

LisaRomeo8
[(6, (3.30014605104868e-09+0j))]
3.30014605104868e-09
1

DrMaryJung
[(31, 4.615791899290713e-06)]
4.615791899290713e-06
1

IndiaDST
[(7, 3.7422067352823e-05), (15, (7.192993510694289e-13+0j)), (18, (9.133494908773223e-11+0j))]
3.7422159407071434e-05
3

TOIMumbai
[(29, (1.1277857207189301e-07+0j))]
1.1277857207189301e-07
1

conradcreates
[(20, (8.370688371761311e-15+0j))]
8.370688371761311e-15
1

sdrosetype1
[(17, (3.1398321220095175e-12+0j))]
3.1398321220095175e-12
1

TheSpicyRD
[(3, (5.223876524539304e-16+0j))]
5.223876524539304e-16
1

geoffscameras
[(7, (4.645146554307411e-18+0j))]
4.645146554307411e-18
1

thechiefunicorn
[(21, (5.674562910372441e-10+0j)), (25, (2.5035759752370386e-13+0j)), (26, (5.871542388221406e-17+0j))]
5.677067073501918e-10
3

VSDC
[(7, (8.660950012109404e-12+0j))]
8.660950012109404e-12
1

JDiabetesMetab
[(4, (7.063109351875089e-10+0j))]
7.063109351875089e-10
1

beefy314
[(9, 2.095865410631

Glob_HL_Academy
[(26, (4.3991331296903687e-17+0j))]
4.3991331296903687e-17
1

erikamarguerite
[(8, (6.60652782495227e-10+0j))]
6.60652782495227e-10
1

Day_of_Design
[(11, (-3.633197782018427e-19-0j))]
-3.633197782018427e-19
1

majohanss
[(32, (4.10567097902072e-17+0j))]
4.10567097902072e-17
1

PatientOnline
[(23, (1.263320021959507e-09+0j))]
1.263320021959507e-09
1

annie_sbk
[(28, (4.5452891166445465e-15+0j))]
4.5452891166445465e-15
1

AkronChildrens
[(4, 1.9995079895833382e-05), (24, (1.2766253579022844e-11+0j)), (29, (5.034449771446818e-05+0j))]
7.033959037655514e-05
3

MazurDO
[(22, 7.399189551805695e-06)]
7.399189551805695e-06
1

IvisonJ
[(25, (9.549953849695204e-15+0j))]
9.549953849695204e-15
1

swissmistress
[(5, (1.2207274325353999e-19+0j))]
1.2207274325353999e-19
1

RepSires
[(22, 1.2631206659172151e-05)]
1.2631206659172151e-05
1

andreaedurkin
[(29, (4.297868129351555e-11+0j))]
4.297868129351555e-11
1

AskAnshul
[(24, (3.273002103054595e-15+0j))]
3.273002103054595e-15
1

Rise

[('Healthy4LifeDoc', 0.20583245753868262, 24),
 ('shrimpfingers', 0.032838187129053294, 1),
 ('sensimeliajah', 0.03075734306454536, 6),
 ('MedicalVids', 0.02863641573650292, 2),
 ('MichaelBlackson', 0.027655942123341277, 1),
 ('Ryan_McCran', 0.02763988045702768, 1),
 ('Kidney__Disease', 0.027558774987075176, 2),
 ('judyannewolff', 0.026816017856803064, 1),
 ('Cyarine', 0.02593517973386812, 1),
 ('alldiabetesnews', 0.02458074232726231, 32),
 ('baeryl', 0.022722040057691514, 1),
 ('pbroo003', 0.022322409233093792, 7),
 ('Listen2Lena', 0.02185117731118697, 2),
 ('Atul_Gawande', 0.021121547894259258, 3),
 ('Mikel_Jollett', 0.01953353159509237, 3),
 ('SyedSaddiq', 0.0180710764863133, 1),
 ('kenklippenstein', 0.017287612821715374, 1),
 ('WHO', 0.01666285467881288, 9),
 ('funder', 0.01594146085675269, 1),
 ('michaelwhitney', 0.01099903875692463, 1),
 ('BlvckGrip', 0.008599274234417016, 1),
 ('CMattocks1', 0.00760760501204355, 25),
 ('Diabetescouk', 0.0072502709907377874, 33),
 ('Bethenny', 0.

In [14]:
# consider only scores of people with at least tweets of 10 weeks
#aggregated_scores_filtered = [tup for tup in aggregated_scores if tup[2] > 15]
aggregated_scores_filtered = [tup for tup in aggregated_scores]

#aggregated_scores_filtered

In [15]:
aggregated_scores_filtered

[('Healthy4LifeDoc', 0.20583245753868262, 24),
 ('shrimpfingers', 0.032838187129053294, 1),
 ('sensimeliajah', 0.03075734306454536, 6),
 ('MedicalVids', 0.02863641573650292, 2),
 ('MichaelBlackson', 0.027655942123341277, 1),
 ('Ryan_McCran', 0.02763988045702768, 1),
 ('Kidney__Disease', 0.027558774987075176, 2),
 ('judyannewolff', 0.026816017856803064, 1),
 ('Cyarine', 0.02593517973386812, 1),
 ('alldiabetesnews', 0.02458074232726231, 32),
 ('baeryl', 0.022722040057691514, 1),
 ('pbroo003', 0.022322409233093792, 7),
 ('Listen2Lena', 0.02185117731118697, 2),
 ('Atul_Gawande', 0.021121547894259258, 3),
 ('Mikel_Jollett', 0.01953353159509237, 3),
 ('SyedSaddiq', 0.0180710764863133, 1),
 ('kenklippenstein', 0.017287612821715374, 1),
 ('WHO', 0.01666285467881288, 9),
 ('funder', 0.01594146085675269, 1),
 ('michaelwhitney', 0.01099903875692463, 1),
 ('BlvckGrip', 0.008599274234417016, 1),
 ('CMattocks1', 0.00760760501204355, 25),
 ('Diabetescouk', 0.0072502709907377874, 33),
 ('Bethenny', 0.

In [17]:
import datetime
format = "%Y-%m-%d_%H-%M-%S"

pathname = "authority_scores_sorted_all_{}.csv".format(datetime.datetime.now().strftime(format))
with open(pathname,'w') as file:
    file.write("User;score;number_of_weeks\n")
    for tup1, tup2, tup3 in aggregated_scores_filtered:
        s = str(tup1)+";"+str(tup2)+";"+str(tup3)+";"+"\n"
        file.write(s)

In [184]:
v

score
allnaturalideas  0.000342
IrishBabyFairy   0.000342
Chilari          0.000342
Top_3_Diets      0.000342
CarolynRamsamy   0.000342
zennanni         0.000342
SharonPalmerRD   0.000342
t1international  0.000445
DrDonnyRobinson  0.000080
DiabetesBros     0.000139
erpfiester       0.000331
ThomasKlineMD    0.000371
RannaDylin       0.000909
moIokoplus       0.000120
T1DF_advocacy    0.000414
Jandelliott      0.000318
MathengeMaina2   0.000318
GilmerHealthLaw  0.000318
MEDlCALVIDOEOS   0.000525
MedicaIGuide     0.000022
TheMedicalVids   0.000108
MedicalVids      0.000715
brendanphyland   0.000202
afrezzauser      0.000764
AfrezzaArmy      0.000202
afrezzamom       0.000202
cutthebsgirl     0.000228
RunnerNwizard    0.000228
meggersmckinley  0.000456
iamfrench        0.000456
...                   ...
HealingMB        0.000003
AARPadvocates    0.000017
CeeCeeThunder    0.001000
TopherSpiro      0.000010
MeetLaFT         0.000261
fabioteti1       0.000423
kcphaeton        0.000084
AdamLasher       0.000600
PBlueNovember    0.000554
7NewsMelbourne   0.000131
daniel_kraft     0.000342
imbutho          0.000342
Health4Diabetes  0.000423
diabetesabordo   0.000261
diabeticswithed  0.000456
DiabulimiaHelp   0.000228
ADA_DiabetesPro  0.000342
equitylist       0.000342
diabetesDomin8r  0.000342
DiabetesSecret   0.000342
endocrinenetwrk  0.000342
jpbettger        0.000342
sitapati         0.000342
BizSpark_AU      0.000342
DiabetesMine     0.000484
team_resolute    0.000200
MedtechTalk      0.000423
AbbottGlobal     0.000261
adam_tau         0.000680
type1girl        0.000005

[74 rows x 1 columns]